In [ ]:
"""
Notebook containing QR and QRCP algorithm implementations

The following algorithms are implemented

The following algorithms are in progress
  1. HouseHolder QR with BLAS-1
      - other version (2-4)
  2. HouseHolder QR with BLAS-2
      - other version (2-4)
  3. HouseHolder QR with BLAS-3 (with WY blocked representation)
  4. HouseHolder QR with BLAS-3 (with compact WY, or YT, blocked representation)
  5. Gram-Schmidt QR with BLAS-1
      - need it to handle rectangular matrices
      - figure out why version 3 is wack
  6. Gram-Schmidt QR with BLAS-2
      - need it to handle rectangular matrices
      - finish version 2
      - finish version 3
  10. HouseHolder QR with column-pivoting with BLAS-1
      - more robust norm-update scheme to avoid cancellation
      - finish other versions
  11. HouseHolder QR with column-pivoting with BLAS-2
      - more robust norm-update scheme to avoid cancellation
      - finish other versions
  12. HouseHolder QR with column-pivoting with BLAS-3
      - other two Connector-matrix representation versions
  16. Single-sampled Randomized QRCP
  17. Repeated-sampled Randomized QRCP
  18. Randomized QRCP
  19. Truncated Randomized QRCP

The following algorithms need to be implemented 

The following algorithms would be fun to implement later but are not important now:
  7. Gram-Schmidt QR with BLAS-3
  8. FLAME notation unblocked HouseHolder QR
  9. FLAME notation blocked HouseHolder QR (with alternate blocked representation)
  13. FLAME notation HouseHolder QR with column-pivoting
  15. Jed/Ming HouseHolder QR with column pivoting BLAS-3

  Extra:
    experiment with different precision
    try using CholeskyQR instead of QRCP for the short and fat panel
"""

In [ ]:
# Import all of the necessary libraries
import numpy as np
import numpy.linalg as la
import sys
import time
import matplotlib.pyplot as ppt

In [ ]:
"""
5. Gram-Schmidt QR with BLAS-1 implementations

   3 different versions: 1) Iterative
                         2) Recursive
"""

def Gram_Schmidt_QR_BLAS1_version_1(A):
    numColumns = A.shape[1]
    R = np.zeros((numColumns, numColumns))
    
    for i in range(numColumns):
        orthDirLen = la.norm(A[:,i],2)
        A[:,i] = A[:,i]/orthDirLen
        R[i,i] = orthDirLen
        # subtract out components of the remaining pool of vectors that lie in same
        #   direction as A[:,i]
        for j in range(i+1,numColumns):
            subLen = np.dot(A[:,j], A[:,i])
            A[:,j] = A[:,j] - subLen*A[:,i]
            R[i,j] = subLen                 
    
    # A has been transformed into Q, as Gram-Schmidt is a triangular orthogonalization algorithm
    return (A,R)


# Recursive helper function for version 2 below
def Gram_Schmidt_QR_BLAS1_version_2_backtrack(A,R, numColumns, currColumn):
    # recursive base case
    if (currColumn == numColumns):
        return (A,R)
    
    orthDirLen = la.norm(A[:,currColumn],2)
    A[:,currColumn] = A[:,currColumn]/orthDirLen
    R[currColumn,currColumn] = orthDirLen
    # subtract out components of the remaining pool of vectors that lie in same
    #   direction as A[:,i]
    for j in range(currColumn+1,numColumns):
        subLen = np.dot(A[:,j], A[:,currColumn])
        A[:,j] = A[:,j] - subLen*A[:,currColumn]
        R[currColumn,j] = subLen                 
    
    # A has been transformed into Q, as Gram-Schmidt is a triangular orthogonalization algorithm
    return Gram_Schmidt_QR_BLAS1_version_2_backtrack(A,R,numColumns,currColumn+1)

# Python is a bit weird with references, and I like to use references with recursive backtracking algorithms
def Gram_Schmidt_QR_BLAS1_version_2(A):
    numColumns = A.shape[1]
    R = np.zeros((numColumns, numColumns))
    return Gram_Schmidt_QR_BLAS1_version_2_backtrack(A,R,numColumns,0)

def Gram_Schmidt_QR_BLAS1_version_3(A):
    numColumns = A.shape[1]
    R = np.eye(numColumns)
    
    for i in range(numColumns):
        R_current = np.eye(numColumns)
        orthDirLen = la.norm(A[:,i],2)
        R_current[i,i] = orthDirLen
        # subtract out components of the remaining pool of vectors that lie in same
        #   direction as A[:,i]
        for j in range(i+1,numColumns):
            subLen = np.dot(A[:,j], A[:,i])
            R_current[i,j] = (-1)*subLen
        R = np.dot(R,R_current)
    
    # A has been transformed into Q, as Gram-Schmidt is a triangular orthogonalization algorithm
    
    return (np.dot(A,R),la.inv(R))

In [ ]:
"""
5. Gram-Schmidt QR with BLAS-1 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
Q,R = Gram_Schmidt_QR_BLAS1_version_2(A)
#print(Q)
#print(R)
#print(la.norm(np.eye(numColumns) - np.dot(Q.T,Q)))

# Test deviation from orthogonality
# Test residual
"""

In [ ]:
"""
6. Gram-Schmidt QR with BLAS-2 implementations

   3 different versions: 1) Iterative
                         2) Recursive
                         3) Matrix-notation
"""

def Gram_Schmidt_QR_BLAS2_version_1(A):
    numColumns = A.shape[1]
    R = np.eye(numColumns)
    
    for i in range(numColumns):
        orthDirLen = la.norm(A[:,i],2)
        R[i,i] = orthDirLen
        A[:,i] = A[:,i]/orthDirLen
        stupidTransposeColumn = np.array([A[:,i]])
        #print stupidTransposeColumn.shape
        #print A[:,(i+1):].shape
        lengthRow = np.dot(stupidTransposeColumn, A[:,(i+1):])
        R[i, (i+1):] = lengthRow
        A[:,(i+1):] = A[:,(i+1):] - np.outer(A[:,i], lengthRow)
    return (A,R)

In [ ]:
"""
6. Gram-Schmidt QR with BLAS-2 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
Q,R = Gram_Schmidt_QR_BLAS2_version_1(A)
print(Q)
print(R)
print(la.norm(np.eye(numColumns) - np.dot(Q.T,Q)))

# Test deviation from orthogonality
# Test residual
"""

In [ ]:
"""
FUNCTION: convertReflectorsToOrthgonal_version_1(Reflectors)
This function is needed to reconstruct Q from the reflectors that are stored explicitely,
  since the concatenation of reflectors is NOT the orthogonal matrix

Idea: To explicitely form Q, we need to do: Q*I = Q, where the left Q is defined implicitely using the 
       reflectors. The Q on the right will be defined explicitely via repeated Blas-2 operations
"""
def convertReflectorsToOrthgonal_version_1(Reflectors):
    numRows = Reflectors.shape[0]
    numColumns = Reflectors.shape[1]
    # Q must be square now, instead of reduced
    newQ = np.eye(numRows)
    # Iterate backwards over the reflectors
    for i in range(numColumns-1,-1,-1):
        #print(Reflectors[:,i])
        tau = 2./(np.dot(Reflectors[:,i], Reflectors[:,i]))
        #print "shape of Reflector - ", Reflectors[:,i][:,np.newaxis].T.shape, " and shape of newQ - ", newQ.shape
        tempMatrix = np.dot(Reflectors[:,i][:,np.newaxis].T,newQ)
        newQ = newQ - np.dot(tau*Reflectors[:,i][:,np.newaxis],tempMatrix)
    return newQ

"""
FUNCTION: convertReflectorsToOrthgonal_version_2(Reflectors)
This function is needed to reconstruct Q from the reflectors that are stored in the lower-trapezoidal
   part of matrix A->R. We also have a vector that stores the first elements that would need to have lived
   on the diagonals, but were not able to be stored because we also needed to store the diagonal elements of R
"""
def convertReflectorsToOrthgonal_version_2(Reflectors, firstElements):
    return A

"""
Idea: Same as version_1, except we want to form Q-transpose, not Q
"""
def convertReflectorsToOrthgonal_version_3(Reflectors):
    numRows = Reflectors.shape[0]
    numColumns = Reflectors.shape[1]
    # Q must be square now, instead of reduced
    newQ = np.eye(numRows)
    # Iterate backwards over the reflectors
    for i in range(0,numColumns):
        #print(Reflectors[:,i])
        tau = 2./(np.dot(Reflectors[:,i], Reflectors[:,i]))
        #print "shape of Reflector - ", Reflectors[:,i][:,np.newaxis].T.shape, " and shape of newQ - ", newQ.shape
        tempMatrix = np.dot(Reflectors[:,i][:,np.newaxis].T,newQ)
        newQ = newQ - np.dot(tau*Reflectors[:,i][:,np.newaxis],tempMatrix)
    return newQ

In [ ]:
"""
1. HouseHolder QR with BLAS-1 implementations

   3 different versions: 1) Iterative with matrix Q not explicitely stored, reflectors are stored separately
                                -- so Q stores the reflectors, and A'=R stores the upper-triangular portion
                         2) Iterative with matrix Q embedded into A (needs an extra array)
                                 -- So the reflectors are stored in the lower-trapezoidal part of A, R is upper
                         3) Recursive
"""

def HouseHolderQR_BLAS1_version_1(A):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    for i in range(numColumns):
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns one at a time (BLAS-1) to complete the Matrix-Matrix product
        # Lets include the current column, although we could have done that vector transformation individually
        for j in range(i,numColumns):
            A[i:numRows,j] = A[i:numRows,j] - np.dot(tau*Reflectors[i:,i], np.dot(Reflectors[i:,i],A[i:numRows,j]))
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A)

def HouseHolderQR_BLAS1_version_2(A):
    return (A,A)

def HouseHolderQR_BLAS1_version_3(A):
    return (A,A)

In [ ]:
"""
1. HouseHolder QR with BLAS-1 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R = HouseHolderQR_BLAS1_version_1(A)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
"""

In [ ]:
"""
1. HouseHolder QR with BLAS-2 implementations

   3 different versions: 1) Iterative with matrix Q not explicitely stored, reflectors are stored separately
                                -- so Q stores the reflectors, and A'=R stores the upper-triangular portion
                         2) Iterative with matrix Q embedded into A (needs an extra array)
                                 -- So the reflectors are stored in the lower-trapezoidal part of A, R is upper
                         3) Recursive
"""

def HouseHolderQR_BLAS2_version_1(A):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    for i in range(numColumns):
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns all at once (BLAS-2) to complete the Matrix-Matrix product
        A[i:,i:] = A[i:,i:] - np.dot(tau*Reflectors[i:,i][:,np.newaxis], np.dot(Reflectors[i:,i][:,np.newaxis].T, A[i:,i:]))
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A)

def HouseHolderQR_BLAS2_version_2(A):
    return (A,A)

def HouseHolderQR_BLAS2_version_3(A):
    return (A,A)


In [ ]:
"""
1. HouseHolder QR with BLAS-2 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R = HouseHolderQR_BLAS2_version_1(A)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
"""

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-1 implementations

   3 different versions: 1) Iterative with matrix Q not explicitely stored, reflectors are stored separately
                                -- so Q stores the reflectors, and A'=R stores the upper-triangular portion
                         2) Iterative with matrix Q embedded into A (needs an extra array)
                                 -- So the reflectors are stored in the lower-trapezoidal part of A, R is upper
                         3) Recursive
                         4) Same as version 1 except it can detect rank
"""

def HouseHolderQRCP_BLAS1_version_1(A, numPivots):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal

    # Only tasked to find the first numPivots pivot columns
    for i in range(numPivots):
        # Find next column pivot (lets just use naive scan instead of a heap or something)
        
        pivotIndex = np.argmax(norms[i:])+i
        kingNorm = np.amax(norms[i:])

#        pivotIndex = i
#        kingNorm = 0
#        for j in range(i,numColumns):
#            if (norms[j] > kingNorm):
#                kingNorm = norms[j]
#                pivotIndex = j

        #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
        # Swap out pivot column with current column
        # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
        tempColumn = A[:,i].copy()     # avoid overwriting via nasty pass by reference?
        A[:,i] = A[:,pivotIndex].copy() # same thing as above
        A[:,pivotIndex] = tempColumn
        savePermIndex = permutationIndices[pivotIndex].copy()
        permutationIndices[pivotIndex] = permutationIndices[i].copy()
        permutationIndices[i] = savePermIndex
        tempNorm = norms[pivotIndex].copy()
        norms[pivotIndex] = norms[i].copy()
        norms[i] = tempNorm.copy()
        
        # Continue on with typical Householder QR
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        #print "check this dot product - ", np.dot(Reflectors[i:,i],Reflectors[i:,i])
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns one at a time (BLAS-1) to complete the Matrix-Matrix product
        # Lets include the current column, although we could have done that vector transformation individually
        for j in range(i,numColumns):
            A[i:,j] = A[i:,j] - np.dot(tau*Reflectors[i:,i], np.dot(Reflectors[i:,i],A[i:,j]))
            # We can merge loop and update the column norm right here
            # But we should find an update scheme that doesn't have cancellation possibility
            norms[j] = norms[j] - A[i,j]**2
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A,permutationIndices)

def HouseHolderQRCP_BLAS1_version_2(A):
    return (A,A)

def HouseHolderQRCP_BLAS1_version_3(A):
    return (A,A)

def HouseHolderQRCP_BLAS1_version_4(A, tolerance):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    rankEstimate = numColumns
    
    # Only tasked to find the first numPivots pivot columns
    for i in range(numColumns):
        # Find next column pivot (lets just use naive scan instead of a heap or something)
        
        pivotIndex = np.argmax(norms[i:])+i
        kingNorm = np.amax(norms[i:])
        
        # Detect rank!
        if (kingNorm < tolerance):
            rankEstimate = i
            break

#        pivotIndex = i
#        kingNorm = 0
#        for j in range(i,numColumns):
#            if (norms[j] > kingNorm):
#                kingNorm = norms[j]
#                pivotIndex = j

        #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
        # Swap out pivot column with current column
        # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
        tempColumn = A[:,i].copy()     # avoid overwriting via nasty pass by reference?
        A[:,i] = A[:,pivotIndex].copy() # same thing as above
        A[:,pivotIndex] = tempColumn
        savePermIndex = permutationIndices[pivotIndex].copy()
        permutationIndices[pivotIndex] = permutationIndices[i].copy()
        permutationIndices[i] = savePermIndex
        tempNorm = norms[pivotIndex].copy()
        norms[pivotIndex] = norms[i].copy()
        norms[i] = tempNorm.copy()
        
        # Continue on with typical Householder QR
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        #print "check this dot product - ", np.dot(Reflectors[i:,i],Reflectors[i:,i])
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns one at a time (BLAS-1) to complete the Matrix-Matrix product
        # Lets include the current column, although we could have done that vector transformation individually
        for j in range(i,numColumns):
            A[i:,j] = A[i:,j] - np.dot(tau*Reflectors[i:,i], np.dot(Reflectors[i:,i],A[i:,j]))
            # We can merge loop and update the column norm right here
            # But we should find an update scheme that doesn't have cancellation possibility
            norms[j] = norms[j] - A[i,j]**2
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    
    # If this matrix is low-rank, we need to obtain R_22 manually
    # Above is wrong -- Don't listen. We have already been updating properly at each iteration
#    if (rankEstimate < numColumns):
#        Q_approx = convertReflectorsToOrthgonal_version_1(ReflectorsCopy[:,:(rankEstimate+1)])
#        A[:rankEstimate,rankEstimate:] = np.dot(Q_approx[:,:rankEstimate].T, A[:,rankEstimate:])
    return (Reflectors,A,permutationIndices,rankEstimate)

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-1 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R,P = HouseHolderQRCP_BLAS1_version_1(A, numColumns)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

#print np.eye(numColumns)[:,P]

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
"""

In [ ]:
"""
1. Rank-detecting HouseHolder QR with column pivoting with BLAS-1 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
testRank = input("What rank matrix do you want to test with: ")
U,D,V = la.svd(A,0)

for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0
# Re-form A with rank testRank
tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)
# figure out how to deal  with detecting rank
Reflectors,R,P,rankEstimate = HouseHolderQRCP_BLAS1_version_4(A, 1e-13)
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])
# Test deviation from orthogonality
# Test residual
print "Rank estimate - ", rankEstimate
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],np.dot(R[:rankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0
tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
"""

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-2 implementations

   3 different versions: 1) Iterative with matrix Q not explicitely stored, reflectors are stored separately
                                -- so Q stores the reflectors, and A'=R stores the upper-triangular portion
                         2) Iterative with matrix Q embedded into A (needs an extra array)
                                 -- So the reflectors are stored in the lower-trapezoidal part of A, R is upper
                         3) Recursive
                         4) Same as version 1 except it can detect rank
"""

def HouseHolderQRCP_BLAS2_version_1(A,numPivots):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    
    # Only tasked to find the first numPivots pivot columns
    for i in range(numPivots):
        # Find next column pivot (lets just use naive scan instead of a heap or something)
        
        pivotIndex = np.argmax(norms[i:])+i
        kingNorm = np.amax(norms[i:])
        
#        pivotIndex = i
#        kingNorm = 0
#        for j in range(i,numColumns):
#            if (norms[j] > kingNorm):
#                kingNorm = norms[j]
#                pivotIndex = j
        
        #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
        # Swap out pivot column with current column
        # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
        tempColumn = A[:,i].copy()     # avoid overwriting via nasty pass by reference?
        A[:,i] = A[:,pivotIndex].copy() # same thing as above
        A[:,pivotIndex] = tempColumn
        savePermIndex = permutationIndices[pivotIndex].copy()
        permutationIndices[pivotIndex] = permutationIndices[i].copy()
        permutationIndices[i] = savePermIndex
        tempNorm = norms[pivotIndex].copy()
        norms[pivotIndex] = norms[i].copy()
        norms[i] = tempNorm.copy()
        
        # Continue on with typical Householder QR
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns all at once (BLAS-2) to complete the Matrix-Matrix product
        # Lets include the current column, although we could have done that vector transformation individually
        A[i:,i:] = A[i:,i:] - np.dot(tau*Reflectors[i:,i][:,np.newaxis], np.dot(Reflectors[i:,i][:,np.newaxis].T, A[i:,i:]))
        for j in range(i,numColumns):
            # But we should find an update scheme that doesn't have cancellation possibility
            norms[j] = norms[j] - A[i,j]**2
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A,permutationIndices)

def HouseHolderQRCP_BLAS2_version_2(A):
    return (A,A)

def HouseHolderQRCP_BLAS2_version_3(A):
    return (A,A)

def HouseHolderQRCP_BLAS2_version_4(A,tolerance):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    rankEstimate = numColumns
    
    # Only tasked to find the first numPivots pivot columns
    for i in range(numColumns):
        # Find next column pivot (lets just use naive scan instead of a heap or something)
        
        pivotIndex = np.argmax(norms[i:])+i
        kingNorm = np.amax(norms[i:])
        
        # Detect rank!
        if (kingNorm < tolerance):
            rankEstimate = i
            break
        
#        pivotIndex = i
#        kingNorm = 0
#        for j in range(i,numColumns):
#            if (norms[j] > kingNorm):
#                kingNorm = norms[j]
#                pivotIndex = j
        
        #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
        # Swap out pivot column with current column
        # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
        tempColumn = A[:,i].copy()     # avoid overwriting via nasty pass by reference?
        A[:,i] = A[:,pivotIndex].copy() # same thing as above
        A[:,pivotIndex] = tempColumn
        savePermIndex = permutationIndices[pivotIndex].copy()
        permutationIndices[pivotIndex] = permutationIndices[i].copy()
        permutationIndices[i] = savePermIndex
        tempNorm = norms[pivotIndex].copy()
        norms[pivotIndex] = norms[i].copy()
        norms[i] = tempNorm.copy()
        
        # Continue on with typical Householder QR
        dirLen = la.norm(A[i:,i],2)   # Don't worry about the first i rows.
        # Below: there could probably be a faster way to do this than to create an identity matrix
        #   at each iteration
        # curReflector points from vector a to norm(a)*e_1, just via vector addition
        # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
        #   first element of the saxpy
        Reflectors[i:,i] = np.sign(A[i,i])*(-1)*dirLen*np.eye(numRows-i)[0:numRows-i,0] - A[i:,i]
        tau = 2./(np.dot(Reflectors[i:,i],Reflectors[i:,i]))
        # update trailing columns all at once (BLAS-2) to complete the Matrix-Matrix product
        # Lets include the current column, although we could have done that vector transformation individually
        A[i:,i:] = A[i:,i:] - np.dot(tau*Reflectors[i:,i][:,np.newaxis], np.dot(Reflectors[i:,i][:,np.newaxis].T, A[i:,i:]))
        for j in range(i,numColumns):
            # But we should find an update scheme that doesn't have cancellation possibility
            norms[j] = norms[j] - A[i,j]**2
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A,permutationIndices,rankEstimate)

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-2 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R,P = HouseHolderQRCP_BLAS2_version_1(A, numColumns)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
"""

In [ ]:
"""
1. Rank-detecting HouseHolder QR with column pivoting with BLAS-1 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
A = np.random.rand(numRows, numColumns)
testRank = input("What rank matrix do you want to test with: ")
U,D,V = la.svd(A,0)

for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0
# Re-form A with rank testRank
tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)
# figure out how to deal  with detecting rank
Reflectors,R,P,rankEstimate = HouseHolderQRCP_BLAS2_version_4(A, 1e-13)
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])
# Test deviation from orthogonality
# Test residual
print "Rank estimate - ", rankEstimate
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],np.dot(R[:rankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0
tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
"""

In [ ]:
"""
1. HouseHolder QR with BLAS-3 implementationS

   3 different versions: 1) Use compact WY connector matrix
                         2) Use UT connector matrix (from FLAME group)
                         3) Use connector matrix proposed by Ming/Duersch paper
"""

def HouseHolderQR_BLAS3_version_1(A, blockSize):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    # Late change: I will make Connector matrix have outside scope so that I can return it
    #  because in TRQRCP, I need the square Connector from the panel
    Connector = np.zeros((blockSize, blockSize))
    
    # Iterate and jump by blockSize
    for i in range(0,numColumns,blockSize):
        # Perform BLAS-2 operations to build up the delayed reflectors before updating
        #  the trailing matrix with the BLAS-3 operation
        
        # We build up the reflector matrix as we iterate over the block
        Connector = np.zeros((min(blockSize,numColumns-i),min(blockSize,numColumns-i)))
        curBlockIndex = -1
        for j in range(i,min(i+blockSize, numColumns)):
            curBlockIndex = curBlockIndex + 1
            # First, before we form our reflector from the pivot vector, we need to accumulate the delayed
            #  reflectors into it. This is a bLAS-2 operation, but the reflector rank update is building up
            #  with each iteration
            
            # Lets break this block up, because we don't need to accumulate reflector updates
            #   into the first column of the block
            if (curBlockIndex > 0):
                # update current column, this will fill out the elements above its diagonal
                #   corresponding to R
                # We must update the ENTIRE column from A[i:,j], not just A[j:,j] -- very important
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, A[i:,j])
#                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex].T, tempMatrix1)
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex].T, tempMatrix1)
                tempMatrix3 = np.dot(Reflectors[i:,i:j], tempMatrix2)
                A[i:,j] = A[i:,j] + tempMatrix3

            # Now, current column will be updated with the rank-(curBlockIndex+1) update and we can calculate reflector
            dirLen = la.norm(A[j:,j],2)   # Don't worry about the first i rows
            # Below: there could probably be a faster way to do this than to create an identity matrix
            #   at each iteration
            # curReflector points from vector a to norm(a)*e_1, just via vector addition
            # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
            #   first element of the saxpy
            Reflectors[j:,j] = np.sign(A[j,j])*(-1)*dirLen*np.eye(numRows-j)[0:numRows-j,0] - A[j:,j]
            tau = 2./(np.dot(Reflectors[j:,j],Reflectors[j:,j]))
            
            # Update current sub-column with reflector to clear out below diagonal
            tempMatrix1 = np.dot(Reflectors[j:,j][:,np.newaxis].T, A[j:,j])
            tempMatrix2 = np.dot(tau*Reflectors[j:,j][:,np.newaxis], tempMatrix1)
            A[j:,j] = A[j:,j] - tempMatrix2
            
            # Lets update the Connector matrix
            Connector[curBlockIndex,curBlockIndex] = (-1)*tau
            # Separate this out if we are on first iteration of block
            if (curBlockIndex > 0):
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, Reflectors[i:,j])
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex], tempMatrix1)
                Connector[0:curBlockIndex, curBlockIndex] = (-1)*tau*tempMatrix2
        # now we can perform BLAS-3 level update with the delayed reflectors on the trailing matrix
        trueBlockSize = min(blockSize, numColumns-i)
        tempMatrix1 = np.dot(Reflectors[i:,i:(i+trueBlockSize)].T, A[i:,(i+trueBlockSize):])
        tempMatrix2 = np.dot(Connector.T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[i:,i:(i+trueBlockSize)], tempMatrix2)
        A[i:,(i+trueBlockSize):] = A[i:,(i+trueBlockSize):] + tempMatrix3
    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,A,Connector)

def HouseHolderQR_BLAS3_version_2(A):
    return (A,A)

def HouseHolderQR_BLAS3_version_3(A):
    return (A,A)

In [ ]:
"""
1. HouseHolder QR with BLAS-3 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R,Connector = HouseHolderQR_BLAS3_version_1(A, blockSize)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
"""

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-3 implementationS

   3 different versions: 1) Use compact WY connector matrix
                         2) Use UT connector matrix (from FLAME group)
                         3) Use connector matrix proposed by Ming/Duersch paper
                         4) Same as version 1 except it can detect rank
"""

def HouseHolderQRCP_BLAS3_version_1(A, blockSize, maxPivots):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    
    # Lets store R explicitely here because of the excruciating pain of dealing with corrupted updates
    # Store in same fashion as A to avoid collateral damage with other functions
    #  Can optimize later
    R = np.zeros((numRows, numColumns))
    
    # Iterate and jump by blockSize
    for i in range(0,maxPivots,blockSize):
        trueBlockSize = min(blockSize, maxPivots-i)
        
        # Perform BLAS-2 operations to build up the delayed reflectors before updating
        #  the trailing matrix with the BLAS-3 operation
        
        # We build up the reflector matrix as we iterate over the block
        Connector = np.zeros((trueBlockSize,trueBlockSize))
        curBlockIndex = -1
        
        # Let's do something innefficient for now: save the first b rows of the submatrix
        # For now, shouldn't have to worry about lower-left triangle being nonzeros, but look there if problems
        for j in range(i,i+trueBlockSize):
            curBlockIndex = curBlockIndex + 1
            # Find next column pivot first (lets just use naive scan instead of a heap or something)
            pivotIndex = np.argmax(norms[j:])+j
            kingNorm = np.amax(norms[j:])

            # This loop could be skipped at a later optimization if the norm update loop below keeps track of the largest column norm after row update
#            for k in range(j,numColumns):
#                if (norms[k] > kingNorm):
#                    kingNorm = norms[k]
#                    pivotIndex = k
            #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
            # Swap out pivot column with current column
            # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
            tempColumn = A[:,j].copy()     # avoid overwriting via nasty pass by reference?
            A[:,j] = A[:,pivotIndex].copy() # same thing as above
            A[:,pivotIndex] = tempColumn.copy()   # just for precaution
            savePermIndex = permutationIndices[pivotIndex].copy()
            permutationIndices[pivotIndex] = permutationIndices[j].copy()
            permutationIndices[j] = savePermIndex.copy()
            tempNorm = norms[pivotIndex].copy()
            norms[pivotIndex] = norms[j].copy()
            norms[j] = tempNorm.copy()
            # Need to also permute R
            # Later optimization: wasteful to permute zeros at bottom partition of matrix
            tempColumn1 = R[:,j].copy()
            R[:,j] = R[:,pivotIndex].copy()
            R[:,pivotIndex] = tempColumn1.copy()

            # First, before we form our reflector from the pivot vector, we need to accumulate the delayed
            #  reflectors into it. This is a bLAS-2 operation, but the reflector rank update is building up
            #  with each iteration
            
            # Lets break this block up, because we don't need to accumulate reflector updates
            #   into the first column of the block
            if (curBlockIndex > 0):
                # update current column in submatrix. The elements of R are NOT FOUND HERE. This is just to attain the reflector
                # We must update the SUB column (just A[j:,j], unlike in non-pivoted BLAS level 3 HQR) -- very important
                #    BUT, we still need to use the "silent" columns of the current column of A and the upper-triangular part of the reflectors
                #      and we do this in a special way by saved the partial products in a separate array
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, A[i:,j])
#                # Add in the 2nd part with the data that was saved and not corrupted to complete the inner products
#                tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:j,i:j].T, saveMatrixRows[0:(j-i), j-i])
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex].T, tempMatrix1)
                tempMatrix3 = np.dot(Reflectors[j:,i:j], tempMatrix2)
                # Its ok to modify A here
                A[j:,j] = A[j:,j] + tempMatrix3

            # Now, current column will be updated with the rank-(curBlockIndex+1) update and we can calculate reflector
            dirLen = la.norm(A[j:,j],2)   # Don't worry about the first i rows
            # Below: there could probably be a faster way to do this than to create an identity matrix
            #   at each iteration
            # curReflector points from vector a to norm(a)*e_1, just via vector addition
            # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
            #   first element of the saxpy
            Reflectors[j:,j] = np.sign(A[j,j])*(-1)*dirLen*np.eye(numRows-j)[0:numRows-j,0] - A[j:,j]
            tau = 2./(np.dot(Reflectors[j:,j],Reflectors[j:,j]))
            
            # Update current sub-column with reflector to clear out below diagonal (could just relace this with setting equal to norm*e1)
            tempMatrix1 = np.dot(Reflectors[j:,j][:,np.newaxis].T, A[j:,j])
            tempMatrix2 = np.dot(tau*Reflectors[j:,j][:,np.newaxis], tempMatrix1)
#            A[j:,j] = A[j:,j] - tempMatrix2
            # Lets modify R instead of A
            R[j:,j] = A[j:,j] - tempMatrix2
#            print "Current subcolumn of R - ", R
#            print "check this value - ", R[:,0] - np.dot(tau*Reflectors[j:,j][:,np.newaxis], np.dot(Reflectors[j:,j][:,np.newaxis].T, R[:,0]))
            
            # Lets update the Connector matrix
            Connector[curBlockIndex,curBlockIndex] = (-1)*tau
            # Separate this out if we are on first iteration of block
            if (curBlockIndex > 0):
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, Reflectors[i:,j])
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex], tempMatrix1)
                Connector[0:curBlockIndex, curBlockIndex] = (-1)*tau*tempMatrix2
        
            # Before we can update the norms, we need to update the current row so that we can make an informed pivot choice
            # Possible problem: we might need the non-updated part of A when performing these updates to get coefficients to scale the reflectors
            # Problem fixed (temporarily) as we are now storing R explicitely so the rows needed of A are not getting corrupted
            tempMatrix1 = np.dot(Reflectors[i:,i:(j+1)].T, A[i:,(j+1):])
            # we need the fix here too, since if we use the first j-i columns in the product above, we are using overwritten values,
            #   so we need to use the saved partial products and sum them up to complete the inner products
#            if (curBlockIndex > 0):
#                tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:j,i:(j+1)].T, saveMatrixRows[0:(j-i), (j-i+1):])
            tempMatrix2 = np.dot(Connector[0:(curBlockIndex+1),0:(curBlockIndex+1)].T, tempMatrix1)
            tempMatrix3 = np.dot(Reflectors[j,i:(j+1)], tempMatrix2)
            # Store into R, not A!!!
            R[j,(j+1):] = A[j,(j+1):] + tempMatrix3
            
            for j in range(j,numColumns):
                # But we should find an update scheme that doesn't have cancellation possibility
                # Use R here, not A!!!
                norms[j] = norms[j] - R[i,j]**2
        
        # now we can perform BLAS-3 level update with the delayed reflectors on the trailing matrix
        trueBlockSize = min(blockSize, numColumns-i)
        tempMatrix1 = np.dot(Reflectors[i:,i:(i+trueBlockSize)].T, A[i:,(i+trueBlockSize):])
        # Add in the rest of the terms of the inner-product that were saved during the block iteration
        #  before the data needed was overwritten
#        tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:(i+trueBlockSize),i:(i+trueBlockSize)].T, saveMatrixRows[:, blockSize:])
        tempMatrix2 = np.dot(Connector.T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[(i+trueBlockSize):,i:(i+trueBlockSize)], tempMatrix2)
        # Here, we are supposed to store into A, not R!
        A[(i+trueBlockSize):,(i+trueBlockSize):] = A[(i+trueBlockSize):,(i+trueBlockSize):] + tempMatrix3

    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,R,permutationIndices)

def HouseHolderQRCP_BLAS3_version_2(A):
    return (A,A)

def HouseHolderQRCP_BLAS3_version_3(A):
    return (A,A)

def HouseHolderQRCP_BLAS3_version_4(A, blockSize, tolerance, maxPivots):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    permutationIndices = np.arange(numColumns)
    norms = np.zeros((numColumns,1))
    for i in range(numColumns):
        norms[i] = la.norm(A[:,i],2)**2      # power 2 because it helps with update below
    Reflectors = np.zeros((numRows, numColumns))   # will be upper-trapezoidal
    rankEstimate = numColumns
    
    # Lets store R explicitely here because of the excruciating pain of dealing with corrupted updates
    # Store in same fashion as A to avoid collateral damage with other functions
    #  Can optimize later
    R = np.zeros((numRows, numColumns))
    
    # Iterate and jump by blockSize
    for i in range(0,numColumns,blockSize):
        trueBlockSize = min(blockSize, numColumns-i)
        
        # Perform BLAS-2 operations to build up the delayed reflectors before updating
        #  the trailing matrix with the BLAS-3 operation
        
        # We build up the reflector matrix as we iterate over the block
        Connector = np.zeros((trueBlockSize,trueBlockSize))
        curBlockIndex = -1
        foundRank = False   # flag for info once out of inner loop
        
        # Let's do something innefficient for now: save the first b rows of the submatrix
        # For now, shouldn't have to worry about lower-left triangle being nonzeros, but look there if problems
        for j in range(i,i+trueBlockSize):
            curBlockIndex = curBlockIndex + 1
            # Find next column pivot first (lets just use naive scan instead of a heap or something)
            pivotIndex = np.argmax(norms[j:])+j
            kingNorm = np.amax(norms[j:])
            
            # Detect rank!
            if (kingNorm < tolerance):
                rankEstimate = j
                foundRank = True
                break
            elif (j >= maxPivots):
                rankEstimate = maxPivots
                FoundRank = True
                break

            # This loop could be skipped at a later optimization if the norm update loop below keeps track of the largest column norm after row update
#            for k in range(j,numColumns):
#                if (norms[k] > kingNorm):
#                    kingNorm = norms[k]
#                    pivotIndex = k
            #print "Pivot column on iteration ", i, " is ", pivotIndex, " with norm value - ", norms[pivotIndex]
            # Swap out pivot column with current column
            # Key question will be answered right here -- do we need to swap out entire column, or just subcolumn?
            tempColumn = A[:,j].copy()     # avoid overwriting via nasty pass by reference?
            A[:,j] = A[:,pivotIndex].copy() # same thing as above
            A[:,pivotIndex] = tempColumn.copy()   # just for precaution
            savePermIndex = permutationIndices[pivotIndex].copy()
            permutationIndices[pivotIndex] = permutationIndices[j].copy()
            permutationIndices[j] = savePermIndex.copy()
            tempNorm = norms[pivotIndex].copy()
            norms[pivotIndex] = norms[j].copy()
            norms[j] = tempNorm.copy()
            # Need to also permute R
            # Later optimization: wasteful to permute zeros at bottom partition of matrix
            tempColumn1 = R[:,j].copy()
            R[:,j] = R[:,pivotIndex].copy()
            R[:,pivotIndex] = tempColumn1.copy()

            # First, before we form our reflector from the pivot vector, we need to accumulate the delayed
            #  reflectors into it. This is a bLAS-2 operation, but the reflector rank update is building up
            #  with each iteration
            
            # Lets break this block up, because we don't need to accumulate reflector updates
            #   into the first column of the block
            if (curBlockIndex > 0):
                # update current column in submatrix. The elements of R are NOT FOUND HERE. This is just to attain the reflector
                # We must update the SUB column (just A[j:,j], unlike in non-pivoted BLAS level 3 HQR) -- very important
                #    BUT, we still need to use the "silent" columns of the current column of A and the upper-triangular part of the reflectors
                #      and we do this in a special way by saved the partial products in a separate array
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, A[i:,j])
#                # Add in the 2nd part with the data that was saved and not corrupted to complete the inner products
#                tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:j,i:j].T, saveMatrixRows[0:(j-i), j-i])
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex].T, tempMatrix1)
                tempMatrix3 = np.dot(Reflectors[j:,i:j], tempMatrix2)
                # Its ok to modify A here
                A[j:,j] = A[j:,j] + tempMatrix3

            # Now, current column will be updated with the rank-(curBlockIndex+1) update and we can calculate reflector
            dirLen = la.norm(A[j:,j],2)   # Don't worry about the first i rows
            # Below: there could probably be a faster way to do this than to create an identity matrix
            #   at each iteration
            # curReflector points from vector a to norm(a)*e_1, just via vector addition
            # Also, we address possible catastrophic cancellation by avoiding subtracting similar values in the
            #   first element of the saxpy
            Reflectors[j:,j] = np.sign(A[j,j])*(-1)*dirLen*np.eye(numRows-j)[0:numRows-j,0] - A[j:,j]
            tau = 2./(np.dot(Reflectors[j:,j],Reflectors[j:,j]))
            
            # Update current sub-column with reflector to clear out below diagonal (could just relace this with setting equal to norm*e1)
            tempMatrix1 = np.dot(Reflectors[j:,j][:,np.newaxis].T, A[j:,j])
            tempMatrix2 = np.dot(tau*Reflectors[j:,j][:,np.newaxis], tempMatrix1)
#            A[j:,j] = A[j:,j] - tempMatrix2
            # Lets modify R instead of A
            R[j:,j] = A[j:,j] - tempMatrix2
#            print "Current subcolumn of R - ", R
#            print "check this value - ", R[:,0] - np.dot(tau*Reflectors[j:,j][:,np.newaxis], np.dot(Reflectors[j:,j][:,np.newaxis].T, R[:,0]))
            
            # Lets update the Connector matrix
            Connector[curBlockIndex,curBlockIndex] = (-1)*tau
            # Separate this out if we are on first iteration of block
            if (curBlockIndex > 0):
                tempMatrix1 = np.dot(Reflectors[i:,i:j].T, Reflectors[i:,j])
                tempMatrix2 = np.dot(Connector[0:curBlockIndex,0:curBlockIndex], tempMatrix1)
                Connector[0:curBlockIndex, curBlockIndex] = (-1)*tau*tempMatrix2
        
            # Before we can update the norms, we need to update the current row so that we can make an informed pivot choice
            # Possible problem: we might need the non-updated part of A when performing these updates to get coefficients to scale the reflectors
            # Problem fixed (temporarily) as we are now storing R explicitely so the rows needed of A are not getting corrupted
            tempMatrix1 = np.dot(Reflectors[i:,i:(j+1)].T, A[i:,(j+1):])
            # we need the fix here too, since if we use the first j-i columns in the product above, we are using overwritten values,
            #   so we need to use the saved partial products and sum them up to complete the inner products
#            if (curBlockIndex > 0):
#                tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:j,i:(j+1)].T, saveMatrixRows[0:(j-i), (j-i+1):])
            tempMatrix2 = np.dot(Connector[0:(curBlockIndex+1),0:(curBlockIndex+1)].T, tempMatrix1)
            tempMatrix3 = np.dot(Reflectors[j,i:(j+1)], tempMatrix2)
            # Store into R, not A!!!
            R[j,(j+1):] = A[j,(j+1):] + tempMatrix3
            
            for k in range(j,numColumns):
                # But we should find an update scheme that doesn't have cancellation possibility
                # Use R here, not A!!!
                norms[k] = norms[k] - R[j,k]**2
        
        if (foundRank):
            break
        
        # now we can perform BLAS-3 level update with the delayed reflectors on the trailing matrix
        trueBlockSize = min(blockSize, numColumns-i)
        tempMatrix1 = np.dot(Reflectors[i:,i:(i+trueBlockSize)].T, A[i:,(i+trueBlockSize):])
        # Add in the rest of the terms of the inner-product that were saved during the block iteration
        #  before the data needed was overwritten
#        tempMatrix1 = tempMatrix1 + np.dot(Reflectors[i:(i+trueBlockSize),i:(i+trueBlockSize)].T, saveMatrixRows[:, blockSize:])
        tempMatrix2 = np.dot(Connector.T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[(i+trueBlockSize):,i:(i+trueBlockSize)], tempMatrix2)
        # Here, we are supposed to store into A, not R!
        A[(i+trueBlockSize):,(i+trueBlockSize):] = A[(i+trueBlockSize):,(i+trueBlockSize):] + tempMatrix3

    # R will be in A, and A should be upper-trapezoidal
    # No explicit Q is being returned, as is the case with HouseHolder orthogonal triangularization methods
    return (Reflectors,R,permutationIndices,rankEstimate)

In [ ]:
"""
1. HouseHolder QR with column pivoting with BLAS-3 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
A = np.random.rand(numRows, numColumns)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
print "condition number of input matrix A - ", la.cond(A)
Reflectors,R,P = HouseHolderQRCP_BLAS3_version_1(A, blockSize, numColumns)
#print R
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
#print "check R - ", R
#print "check P - ", P
#print "check Q - ", Q
#print "check this vector - ", np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))
#print "check this vector, a - ", A_copy
print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
"""

In [ ]:
"""
1. Rank-detecting HouseHolder QR with column pivoting with BLAS-3 external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
A = np.random.rand(numRows, numColumns)
testRank = input("What rank matrix do you want to test with: ")
U,D,V = la.svd(A,0)

for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0
# Re-form A with rank testRank
tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)
# figure out how to deal  with detecting rank
Reflectors,R,P,rankEstimate = HouseHolderQRCP_BLAS3_version_4(A, blockSize,1e-13,numColumns)
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])
# Test deviation from orthogonality
# Test residual
print "Rank estimate - ", rankEstimate
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:rankEstimate].T,Q[:,:rankEstimate])-np.eye(rankEstimate),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],np.dot(R[:rankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0
tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
"""

In [ ]:
# Single-sample randomized QR with column pivoting

# Only 1 version -> not rank detecting. User specifies a rankEstimate that they want to use
# Single-sampled Randomized QRCP does not support rank-detection by its very semantics.
#   That king of support is left to repeated-sampled Randomized QRCP

def SSRQRCP(A,rankEstimate,blockSize,oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = rankEstimate+oversamplingParameter
    # really? Why dont I just store in A? Check that out later
    R = np.zeros((rankEstimate, numColumns))
    
    # Generate the random G.I.I.D matrix using numpy random normal
    Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows))
    Sample = np.dot(Omega, A)
    # Perform QR with column-pivoting solely to find the correct pivot order
    # Later optimization: have QRCP call only iterate over rankEstimate columns
    Reflectors,R_temp,Perm = HouseHolderQRCP_BLAS2_version_1(Sample,rankEstimate)
    # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
    # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
    A = np.dot(A,np.eye(numColumns)[:,Perm])
    # Factor to find the upper-left R_11 upper-triangular matrix
    Reflectors,R_temp,Connector = HouseHolderQR_BLAS3_version_1(A[:,0:rankEstimate],blockSize)
    R[:,:rankEstimate] = R_temp[:rankEstimate,:rankEstimate]   # R_temp is A, don't forget
    # We can use the data we have already to solve for submatrix R_12,
    #  which is all we need to be able to create an approximation to original matrix A.

    # But first we need to recreate Q.T from the reflectors we have
    ReflectorsCopy = Reflectors.copy()  # just for saefty and debugging
    # Try version_3 later to see if it works
    Q = convertReflectorsToOrthgonal_version_1(ReflectorsCopy)
    R[:,rankEstimate:] = np.dot(Q[:,:rankEstimate].T, A[:,rankEstimate:])
    return (Reflectors,R,Perm)

In [ ]:
"""
3. Single-sample randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
approxRank = input("Enter approximation rank: ")
oversamplingParameter = input("Enter oversampling parameter : ")

# Error checking
if (testRank < approxRank):
    sys.exit()

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P = SSRQRCP(A, approxRank, blockSize, oversamplingParameter)
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:approxRank].T,Q[:,:approxRank])-np.eye(approxRank),2)
print "Residual - ", la.norm(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P[:numColumns]]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
# Repeated-sample randomized QR with column pivoting

# Version 1 -- Not rank-detecting. User specifies an approximation rank
# Version 2 -- Rank-detecting to some tolerance

def RSRQRCP_version1(A,rankEstimate,blockSize, oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((rankEstimate, numColumns))
    Reflectors = np.zeros((numRows, rankEstimate))
    Perm = np.arange(numColumns,dtype=int)

    # Iterate over blocks, resampling each time
    for i in range(0,rankEstimate,blockSize):
        trueBlockSize = min(blockSize, rankEstimate-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, rankEstimate)
        columnEndRange = min(i+blockSize, rankEstimate)
        # Generate the random G.I.I.D matrix using numpy random normal
        # Note that the compression matrix gets smaller with each block iteration
        #   as we recurse into smaller submatrices of A
        Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows-rowStartRange))
        Sample = np.dot(Omega, A[rowStartRange:,columnStartRange:])
        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        
        # Later optimization: I could change the blockSize here to utilize BLAS level 3 more, since right now,
        #  blockSize == maxPivots as arguments        
        Reflectors_temp,R_temp,Perm_temp = HouseHolderQRCP_BLAS3_version_1(Sample, trueBlockSize, trueBlockSize)
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])
        
        # Now we need to update the trailing matrix and continue on with next block iteration
        A[rowEndRange:,columnEndRange:] = np.dot(Q[:,trueBlockSize:].T, A[rowStartRange:,columnEndRange:])
    return (Reflectors,R,Perm)

def RSRQRCP_version2(A,blockSize,Tolerance, oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((numRows, numColumns))
    Reflectors = np.zeros((numRows, numColumns))
    Perm = np.arange(numColumns,dtype=int)
    rankEstimate = numColumns

    # Iterate over blocks, resampling each time
    for i in range(0,numColumns,blockSize):
        trueBlockSize = min(blockSize, numColumns-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, numColumns)
        columnEndRange = min(i+blockSize, numColumns)
        # Generate the random G.I.I.D matrix using numpy random normal
        # Note that the compression matrix gets smaller with each block iteration
        #   as we recurse into smaller submatrices of A
        Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows-rowStartRange))
        Sample = np.dot(Omega, A[rowStartRange:,columnStartRange:])
        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        
        # Later optimization: I could change the blockSize here to utilize BLAS level 3 more, since right now,
        #  blockSize == maxPivots as arguments
        Reflectors_temp,R_temp,Perm_temp,rankDetect = HouseHolderQRCP_BLAS3_version_4(Sample, trueBlockSize, Tolerance, trueBlockSize)
        
        # Wait on checking rank, because there is still some background computation
        #   that we need to do if detectRank > 1
        
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])
        
        # Check on rank
        if (rankDetect < trueBlockSize):
            rankEstimate = i+rankDetect
            break
        
        # Now we need to update the trailing matrix and continue on with next block iteration
        A[rowEndRange:,columnEndRange:] = np.dot(Q[:,trueBlockSize:].T, A[rowStartRange:,columnEndRange:])
    return (Reflectors,R,Perm,rankEstimate)

In [ ]:
"""
5. Repeated-sample randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
approxRank = input("Enter approximation rank: ")
oversamplingParameter = input("Enter oversampling parameter : ")

# Error checking
if (testRank < approxRank):
    sys.exit()

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P = RSRQRCP_version1(A, approxRank, blockSize, oversamplingParameter)
#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:approxRank].T,Q[:,:approxRank])-np.eye(approxRank),2)
print "Residual - ", la.norm(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
"""
Rank-detecting Repeated-sample randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
oversamplingParameter = input("Enter oversampling parameter : ")

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P,rankEstimate = RSRQRCP_version2(A, blockSize, 1e-13,oversamplingParameter)
print "Rank estimate - ", rankEstimate

#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:rankEstimate].T,Q[:,:rankEstimate])-np.eye(rankEstimate),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],R[:rankEstimate,:])-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-testRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
# Randomized QR with column pivoting

# Version 1 -- not rank detecting. User passes in an approximation rank
# Version 2 -- rank detecting

def RQRCP_version1(A,rankEstimate,blockSize,oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((rankEstimate, numColumns))
    Reflectors = np.zeros((numRows, rankEstimate))
    Perm = np.arange(numColumns,dtype=int)
    
    # Generate the random G.I.I.D matrix using numpy random normal
    # Note that the compression matrix stays the SAME SIZE through each block iteration.
    #   the only thing that changes is that contributions from factored submatrix get subtracted out
    #   as we recurse into smaller submatrices of A
    Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows))
    Sample = np.dot(Omega, A)

    # Iterate over blocks, resampling each time
    for i in range(0,rankEstimate,blockSize):
        trueBlockSize = min(blockSize, rankEstimate-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, rankEstimate)
        columnEndRange = min(i+blockSize, rankEstimate)
        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        Reflectors_temp,S_temp,Perm_temp = HouseHolderQRCP_BLAS3_version_1(Sample, trueBlockSize, trueBlockSize)
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])
        
        # Now we need to update the trailing matrix and continue on with next block iteration
        A[rowEndRange:,columnEndRange:] = np.dot(Q[:,trueBlockSize:].T, A[rowStartRange:,columnEndRange:])
        
        # Time to update the Sample, subtracting out the components from the submatrix above
        # Don't update unless we have another iteration. Bad matrix alignment occurs otherwise
        if (i+blockSize < rankEstimate):
            Sample = np.zeros((sampleRank,numColumns - i - blockSize))
            Sample[rankEstimate:,:] = S_temp[rankEstimate:sampleRank,blockSize:]
            tempMatrix1 = np.dot(la.inv(R[rowStartRange:rowEndRange,columnStartRange:columnEndRange]), R[rowStartRange:rowEndRange,columnEndRange:])
            tempMatrix2 = np.dot(S_temp[:rankEstimate,:blockSize], tempMatrix1)
            Sample[:rankEstimate,:] = S_temp[:rankEstimate,blockSize:] - tempMatrix2
    
    return (Reflectors,R,Perm)

def RQRCP_version2(A,blockSize,Tolerance,oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((numRows, numColumns))
    Reflectors = np.zeros((numRows, numColumns))
    Perm = np.arange(numColumns,dtype=int)
    rankEstimate = numColumns
    
    # Generate the random G.I.I.D matrix using numpy random normal
    # Note that the compression matrix stays the SAME SIZE through each block iteration.
    #   the only thing that changes is that contributions from factored submatrix get subtracted out
    #   as we recurse into smaller submatrices of A
    Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows))
    Sample = np.dot(Omega, A)

    # Iterate over blocks, resampling each time
    for i in range(0,numColumns,blockSize):
        trueBlockSize = min(blockSize, numColumns-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, numColumns)
        columnEndRange = min(i+blockSize, numColumns)
        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        Reflectors_temp,S_temp,Perm_temp,rankDetect = HouseHolderQRCP_BLAS3_version_4(Sample, trueBlockSize, Tolerance, trueBlockSize)
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])

        # Check on rank
        if (rankDetect < trueBlockSize):
            rankEstimate = i+rankDetect
            break
        
        # Now we need to update the trailing matrix and continue on with next block iteration
        A[rowEndRange:,columnEndRange:] = np.dot(Q[:,trueBlockSize:].T, A[rowStartRange:,columnEndRange:])
        
        # Time to update the Sample, subtracting out the components from the submatrix above
        # Don't update unless we have another iteration. Bad matrix alignment occurs otherwise
        if (i+blockSize < rankEstimate):
            Sample = np.zeros((sampleRank,numColumns - i - blockSize))
            Sample[rankEstimate:,:] = S_temp[rankEstimate:sampleRank,blockSize:]
            tempMatrix1 = np.dot(la.inv(R[rowStartRange:rowEndRange,columnStartRange:columnEndRange]), R[rowStartRange:rowEndRange,columnEndRange:])
            tempMatrix2 = np.dot(S_temp[:rankEstimate,:blockSize], tempMatrix1)
            Sample[:rankEstimate,:] = S_temp[:rankEstimate,blockSize:] - tempMatrix2
    
    return (Reflectors,R,Perm,rankEstimate)

In [ ]:
"""
5. Randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
approxRank = input("Enter approximation rank: ")
oversamplingParameter = input("Enter oversampling parameter: ")

# Error checking
if (testRank < approxRank):
    sys.exit()

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P = RQRCP_version1(A, approxRank, blockSize,oversamplingParameter)
#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:approxRank].T,Q[:,:approxRank])-np.eye(approxRank),2)
print "Residual - ", la.norm(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
"""
Rank-detecting Randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
oversamplingParameter = input("Enter oversampling parameter : ")

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P,rankEstimate = RQRCP_version2(A, blockSize, 1e-13,oversamplingParameter)
print "Rank estimate - ", rankEstimate

#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:rankEstimate].T,Q[:,:rankEstimate])-np.eye(rankEstimate),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],R[:rankEstimate,:])-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-testRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
# Truncated Randomized QR with column pivoting with no trailing matrix update

# Version 1 -- not rank detecting. User passes in an approximation rank
# Version 2 -- rank detecting

def TRQRCP_version1(A,rankEstimate,blockSize,oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((rankEstimate, numColumns))
    Connector = np.zeros((numColumns, numColumns))
    Reflectors = np.zeros((numRows, rankEstimate))
    Perm = np.arange(numColumns,dtype=int)

    # Generate the random G.I.I.D matrix using numpy random normal
    # Note that the compression matrix gets smaller with each block iteration
    #   as we recurse into smaller submatrices of A
    Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows))
    Sample = np.dot(Omega, A)

    # Iterate over blocks, resampling each time
    for i in range(0,rankEstimate,blockSize):
        trueBlockSize = min(blockSize, rankEstimate-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, rankEstimate)
        columnEndRange = min(i+blockSize, rankEstimate)

        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        Reflectors_temp,S_temp,Perm_temp = HouseHolderQRCP_BLAS3_version_1(Sample, trueBlockSize, trueBlockSize)
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Before factoring, we need to accumulate delayed updates into the panel
        tempMatrix1 = np.dot(Reflectors[:,:columnStartRange].T, A[:,columnStartRange:columnEndRange])
        tempMatrix2 = np.dot(Connector[:rowStartRange,:columnStartRange].T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[rowStartRange:,:columnStartRange], tempMatrix2)
        A[rowStartRange:,columnStartRange:columnEndRange] = A[rowStartRange:,columnStartRange:columnEndRange] + tempMatrix3
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # Now we need to build up Connector
        # Separate this out if we are on first iteration of block
        if (i > 0):
            tempMatrix1 = np.dot(Reflectors[:,columnStartRange:columnEndRange], Connector[rowStartRange:rowEndRange,columnStartRange:columnEndRange])
            tempMatrix2 = np.dot(Reflectors[:,:rowStartRange].T, tempMatrix1)
            Connector[:rowStartRange,columnStartRange:columnEndRange] = np.dot(Connector[:rowStartRange,:columnStartRange], tempMatrix2)
        
        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
#        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        
        # We use all rows of A, not just all rows of sub-matrix A, for this complicated update
        tempMatrix1 = np.dot(Reflectors[:,:columnEndRange].T, A[:,columnEndRange:])
        tempMatrix2 = np.dot(Connector[:rowEndRange,:columnEndRange].T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[rowStartRange:rowEndRange,:columnEndRange], tempMatrix2)
        R[rowStartRange:rowEndRange,columnEndRange:] = A[rowStartRange:rowEndRange,columnEndRange:] + tempMatrix3
        
#        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])
        
        # No more need to update the trailing matrix and continue on with next block iteration
        
        # Time to update the Sample, subtracting out the components from the submatrix above
        # Don't update unless we have another iteration. Bad matrix alignment occurs otherwise
        if (i+blockSize < rankEstimate):
            Sample = np.zeros((sampleRank,numColumns - i - blockSize))
            Sample[rankEstimate:,:] = S_temp[rankEstimate:sampleRank,blockSize:]
            tempMatrix1 = np.dot(la.inv(R[rowStartRange:rowEndRange,columnStartRange:columnEndRange]), R[rowStartRange:rowEndRange,columnEndRange:])
            tempMatrix2 = np.dot(S_temp[:rankEstimate,:blockSize], tempMatrix1)
            Sample[:rankEstimate,:] = S_temp[:rankEstimate,blockSize:] - tempMatrix2
    return (Reflectors,R,Perm)

def TRQRCP_version2(A,blockSize,Tolerance,oversamplingParameter):
    numRows = A.shape[0]
    numColumns = A.shape[1]
    sampleRank = blockSize+oversamplingParameter
    R = np.zeros((numColumns, numColumns))
    Connector = np.zeros((numColumns, numColumns))
    Reflectors = np.zeros((numRows, numColumns))
    Perm = np.arange(numColumns,dtype=int)
    rankEstimate = numColumns

    # Generate the random G.I.I.D matrix using numpy random normal
    # Note that the compression matrix gets smaller with each block iteration
    #   as we recurse into smaller submatrices of A
    Omega = np.random.normal(0.0, 1.0, (sampleRank,numRows))
    Sample = np.dot(Omega, A)

    # Iterate over blocks, resampling each time
    for i in range(0,numColumns,blockSize):
        trueBlockSize = min(blockSize, numColumns-i)
        rowStartRange = i
        columnStartRange = i
        rowEndRange = min(i+blockSize, numColumns)
        columnEndRange = min(i+blockSize, numColumns)

        # Perform QR with column-pivoting solely to find the correct pivot order for the next b pivots
        # QRCP can only select blockSize pivot columns
        Reflectors_temp,S_temp,Perm_temp,rankDetect = HouseHolderQRCP_BLAS3_version_4(Sample, trueBlockSize,Tolerance,trueBlockSize)
        # Permute the columns of A so that we can run blocked QR on the sampleRank-size panel of A
        # Note: I might want to only permute with this: Perm[:rankEstimate], but that hit trouble when I tried
        # Note: We are also permuting the columns of R that lie in A above the current submatrix
        # Later optimization: I think this is doing too much work if Perm.size << numColumns

        # Still need to update Perm itself, now that I changed it above to Perm_temp
        # Carefully shuffle the contents in Perm form Perm_temp
        Perm[columnStartRange:] = Perm[columnStartRange:][Perm_temp]
        
        # need to do something here with Permutation  -- Should we only use the trailing ccolumns of A here?
        A[:,i:] = np.dot(A[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        #print "A - ", A
        # either store R explicitely in A, or need to permute R itself
        R[:,i:] = np.dot(R[:,i:],np.eye(numColumns-i)[:,Perm_temp])
        
        # Before factoring, we need to accumulate delayed updates into the panel
        tempMatrix1 = np.dot(Reflectors[:,:columnStartRange].T, A[:,columnStartRange:columnEndRange])
        tempMatrix2 = np.dot(Connector[:rowStartRange,:columnStartRange].T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[rowStartRange:,:columnStartRange], tempMatrix2)
        A[rowStartRange:,columnStartRange:columnEndRange] = A[rowStartRange:,columnStartRange:columnEndRange] + tempMatrix3
        
        # Factor to find the upper-left R_11 upper-triangular matrix
        Reflectors[rowStartRange:,columnStartRange:columnEndRange],R_temp,Connector[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = HouseHolderQR_BLAS3_version_1(A[rowStartRange:,columnStartRange:columnEndRange],trueBlockSize)
        R[rowStartRange:rowEndRange,columnStartRange:columnEndRange] = R_temp[:trueBlockSize,:]   # R_temp is A, don't forget
        # We can use the data we have already to solve for submatrix R_12,
        #  which is all we need to be able to create an approximation to original matrix A.

        # Now we need to build up Connector
        # Separate this out if we are on first iteration of block
        if (i > 0):
            tempMatrix1 = np.dot(Reflectors[:,columnStartRange:columnEndRange], Connector[rowStartRange:rowEndRange,columnStartRange:columnEndRange])
            tempMatrix2 = np.dot(Reflectors[:,:rowStartRange].T, tempMatrix1)
            Connector[:rowStartRange,columnStartRange:columnEndRange] = np.dot(Connector[:rowStartRange,:columnStartRange], tempMatrix2)
        
        # But first we need to recreate Q.T from the reflectors we have
          #ReflectorsCopy = Reflectors.copy()  # just for safety and debugging
        # Try version_3 later to see if it works
#        Q = convertReflectorsToOrthgonal_version_1(Reflectors[rowStartRange:,columnStartRange:columnEndRange])
        
        # We use all rows of A, not just all rows of sub-matrix A, for this complicated update
        tempMatrix1 = np.dot(Reflectors[:,:columnEndRange].T, A[:,columnEndRange:])
        tempMatrix2 = np.dot(Connector[:rowEndRange,:columnEndRange].T, tempMatrix1)
        tempMatrix3 = np.dot(Reflectors[rowStartRange:rowEndRange,:columnEndRange], tempMatrix2)
        R[rowStartRange:rowEndRange,columnEndRange:] = A[rowStartRange:rowEndRange,columnEndRange:] + tempMatrix3
        
#        R[rowStartRange:rowEndRange,columnEndRange:] = np.dot(Q[:,0:trueBlockSize].T, A[i:,columnEndRange:])
        
        # Check on rank
        if (rankDetect < trueBlockSize):
            rankEstimate = i+rankDetect
            break
        
        # No more need to update the trailing matrix and continue on with next block iteration
        
        # Time to update the Sample, subtracting out the components from the submatrix above
        # Don't update unless we have another iteration. Bad matrix alignment occurs otherwise
        if (i+blockSize < rankEstimate):
            Sample = np.zeros((sampleRank,numColumns - i - blockSize))
            Sample[rankEstimate:,:] = S_temp[rankEstimate:sampleRank,blockSize:]
            tempMatrix1 = np.dot(la.inv(R[rowStartRange:rowEndRange,columnStartRange:columnEndRange]), R[rowStartRange:rowEndRange,columnEndRange:])
            tempMatrix2 = np.dot(S_temp[:rankEstimate,:blockSize], tempMatrix1)
            Sample[:rankEstimate,:] = S_temp[:rankEstimate,blockSize:] - tempMatrix2
    return (Reflectors,R,Perm,rankEstimate)

In [ ]:
"""
6. Truncated Randomized QR with column pivoting (with no trailing matrix update) external interface for user to play around
     with timings/performance and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
approxRank = input("Enter approximation rank: ")
oversamplingParameter = input("Enter oversampling parameter: ")

# Error checking
if (testRank < approxRank):
    sys.exit()

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
A_temp = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P = TRQRCP_version1(A, approxRank, blockSize, oversamplingParameter)

# For debugging, lets compare R
#print "Look at this element-wise comparison - ", np.abs(RCopy-R)

#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors)

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:approxRank].T,Q[:,:approxRank])-np.eye(approxRank),2)
print "Residual - ", la.norm(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

#print "check this difference between QR and A - ", np.abs(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P]))

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-approxRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
"""
Rank-detecting Truncated randomized QR with column pivoting external interface for user to play around with timings/performance
     and numerical aspects of the computed factorization
"""

"""
# Call the function
numRows = input("Enter number of rows: ")
numColumns = input("Enter number of columns: ")
blockSize = input("Enter block size: ")
testRank = input("What rank matrix do you want to test with: ")
oversamplingParameter = input("Enter oversampling parameter : ")

A = np.random.rand(numRows, numColumns)

# I need to change the singular values of A in order to vary the numerical rank
#   and properly test this method
U,D,V = la.svd(A,0)
for i in range(numColumns-testRank):
    D[numColumns-i-1] = 0

tempTrunc1 = np.dot(np.diag(D), V)
A = np.dot(U, tempTrunc1)
U1,D1,V1 = la.svd(A,0)

# Copy A because it is corrupted in function call, yet is needed for residual check
A_copy = A.copy()
A_sanity = A.copy()
print "condition number of input matrix A - ", la.cond(A)

# Note: SSRQCP does not return a permutation matrix because that operation is already embedded into the algorithm
Reflectors,R,P,rankEstimate = TRQRCP_version2(A, blockSize, 1e-13,oversamplingParameter)
print "Rank estimate - ", rankEstimate

#print "Reflectors - ", Reflectors
#print "R - ", R
Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:rankEstimate])

# Test deviation from orthogonality
# Test residual
print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:rankEstimate].T,Q[:,:rankEstimate])-np.eye(rankEstimate),2)
print "Residual - ", la.norm(np.dot(Q[:,:rankEstimate],R[:rankEstimate,:])-np.dot(A_copy, np.eye(numColumns)[:,P]),2)

U2,D2,V2 = la.svd(A_sanity,0)
for i in range(numColumns-testRank):
    D2[numColumns-i-1] = 0

tempTrunc2 = np.dot(np.diag(D2), V2)
A_trunc = np.dot(U2, tempTrunc2)
print "Residual of truncated SVD - ", la.norm(A_trunc-A_copy,2)
"""

In [ ]:
# Testing playground

# Test ID inventory
"""
1 - Householder QR, BLAS level 1
2 - Householder QR, BLAS level 2
3 - Householder QR, BLAS level 3
4 - Householder QR with column pivoting, BLAS level 1
5 - Householder QR with column pivoting, BLAS level 2
6 - Householder QR with column pivoting, BLAS level 3
7 - Single-sampled randomized Householder QR with column pivoting
8 - Repeated-sampled randomized Householder QR with column pivoting
9 - Randomized Householder QR with column pivoting
10 - Truncated Randomized QR with column pivoting and no trailing matrix update
"""

moreTests = True
while (moreTests):
    
    # Lets create a playground for non-randomized QRCP first
    # Allow them to detect rank, which is important
    # Call the function
    
    testID = input("Enter the function ID you want to test: (Look at top of cell for directory)")
    if (testID == 1):
        print "You are testing Householder QR, BLAS level 1"
    elif (testID == 2):
        print "You are testing Householder QR, BLAS level 2"
    elif (testID == 3):
        print "You are testing Householder QR, BLAS level 3"
    elif (testID == 4):
        print "You are testing Householder QR with column pivoting, BLAS level 1"
    elif (testID == 5):
        print "You are testing Householder QR with column pivoting, BLAS level 2"
    elif (testID == 6):
        print "You are testing Householder QR with column pivoting, BLAS level 3"
    elif (testID == 7):
        print "You are testing Single-sampled randomized Householder QR with column pivoting"
    elif (testID == 8):
        print "You are testing Repeated-sampled randomized Householder QR with column pivoting"
    elif (testID == 9):
        print "You are testing Randomized Householder QR with column pivoting"
    elif (testID == 10):
        print "You are testing Truncated Randomized Householder QR with column pivoting and no trailing matrix update"
    numRows = input("Enter number of rows: ")
    numColumns = input("Enter number of columns: ")
    # Error check:
    if (numColumns > numRows):
        print """Sorry. Householder QR does not support matrices that are underdetermined. Good news is I am going to implement
                  the truncated SVD that directly follows from the algorithm: Truncated Randomized Householder QR with column pivoting and no trailing matrix update
                  , so I can update this and give you access to that algorithm in the coming weeks."""
        continue
    A = np.random.rand(numRows, numColumns)
    # I need to change the singular values of A in order to vary the numerical rank
    #   and properly test this method
    U,D,V = la.svd(A,0)
    
    if (testID == 1):
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        start1 = time.clock()
        Reflectors,R = HouseHolderQR_BLAS1_version_1(A)
        end1 = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors)
        # Test deviation from orthogonality
        # Test residual
        print "Computation took ", end1-start1, " seconds"
        print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
        print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
    elif (testID == 2):
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        start2 = time.clock()
        Reflectors,R = HouseHolderQR_BLAS2_version_1(A)
        end2 = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors)
        # Test deviation from orthogonality
        # Test residual
        print "Computation took ", end2-start2, " seconds"
        print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
        print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
    elif (testID == 3):
        blockSize = input("Enter block size: ")
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        start3 = time.clock()
        Reflectors,R,Connector = HouseHolderQR_BLAS3_version_1(A, blockSize)
        end3 = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors)
        # Test deviation from orthogonality
        # Test residual
        print "Computation took ", end3-start3, " seconds"
        print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
        print "Residual - ", la.norm(np.dot(Q,R)-A_copy,2)
    elif (testID == 4):
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start41 = time.clock()
            Reflectors,R,P = HouseHolderQRCP_BLAS1_version_1(A, numColumns)
            end41 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end41-start41, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start44 = time.clock()
            Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS1_version_4(A, Tolerance)
            end44 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end44-start44, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 5):
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start51 = time.clock()
            Reflectors,R,P = HouseHolderQRCP_BLAS2_version_1(A, numColumns)
            end51 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end51-start51, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start54 = time.clock()
            Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS2_version_4(A, Tolerance)
            end54 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end54-start54, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 6):
        blockSize = input("Enter block size: ")
        # Error check:
        if (blockSize > numColumns):
            print "You cannot enter a blockSize that is greater than the number of columns. Try again"
            continue
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start61 = time.clock()
            Reflectors,R,P = HouseHolderQRCP_BLAS3_version_1(A, blockSize, numColumns)
            end61 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end61-start61, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q,np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start64 = time.clock()
            Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS3_version_4(A, blockSize, Tolerance, numColumns)
            end64 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end64-start64, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 7):
        blockSize = input("Enter block size: ")
        # Error check:
        if (blockSize > numColumns):
            print "You cannot enter a blockSize that is greater than the number of columns. Try again"
            continue
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        approxRank= input("Specify approximation rank: ")
        oversamplingParameter = input("Specify oversampling parameter: ")
        # Error checking
        if ((rankDecision == 0) and (testRank < approxRank)):
            print "Make sure that the matrix rank is greater than or equal to your approximation rank"
            continue
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        start7 = time.clock()
        Reflectors,R,P = SSRQRCP(A, approxRank, blockSize,oversamplingParameter)
        end7 = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors)
        # Test deviation from orthogonality
        # Test residual
        print "Computation took ", end7-start7, " seconds"
        print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:approxRank].T,Q[:,:approxRank])-np.eye(approxRank),2)
        print "Residual - ", la.norm(np.dot(Q[:,:approxRank],R)-np.dot(A_copy, np.eye(numColumns)[:,P[:numColumns]]),2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-approxRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 8):
        blockSize = input("Enter block size: ")
        # Error check:
        if (blockSize > numColumns):
            print "You cannot enter a blockSize that is greater than the number of columns. Try again"
            continue
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        oversamplingParameter = input("Specify oversampling parameter: ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start81 = time.clock()
            Reflectors,R,P = RSRQRCP_version1(A, approxRank, blockSize,oversamplingParameter)
            end81 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end81-start81, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:approxRank],np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start82 = time.clock()
            Reflectors,R,P,computedRankEstimate = RSRQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
            end82 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end82-start82, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 9):
        blockSize = input("Enter block size: ")
        # Error check:
        if (blockSize > numColumns):
            print "You cannot enter a blockSize that is greater than the number of columns. Try again"
            continue
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        oversamplingParameter = input("Specify oversampling parameter: ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start91 = time.clock()
            Reflectors,R,P = RQRCP_version1(A, approxRank, blockSize,oversamplingParameter)
            end91 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end91-start91, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:approxRank],np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start92 = time.clock()
            Reflectors,R,P,computedRankEstimate = RQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
            end92 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end92-start92, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    elif (testID == 10):
        blockSize = input("Enter block size: ")
        # Error check:
        if (blockSize > numColumns):
            print "You cannot enter a blockSize that is greater than the number of columns. Try again"
            continue
        testRank = input("What rank matrix do you want to test with: ")
        # Error check
        if (testRank > numColumns):
            print "Requested rank must be less than or equal to numColumns"
            continue
        rankDecision= input("Do you want to detect rank dynamically (1), or specify approximation rank explicitely (0)? : ")
        oversamplingParameter = input("Specify oversampling parameter: ")
        for i in range(numColumns-testRank):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check
        A_copy = A.copy()
        A_sanity = A.copy()
        print "condition number of input matrix A - ", la.cond(A)
        # figure out how to deal  with detecting rank
        if (rankDecision == 0):
            approxRank = input("Enter approximation rank if specified above. Otherwise, type anything: ")
            # Error checking
            if ((rankDecision == 0) and (testRank < approxRank)):
                print "Make sure that the matrix rank is greater than or equal to your approximation rank"
                continue
            start10_1 = time.clock()
            Reflectors,R,P = TRQRCP_version1(A, approxRank, blockSize,oversamplingParameter)
            end10_1 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors)
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end10_1-start10_1, " seconds"
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:approxRank],np.dot(R,np.eye(numColumns)[:,P].T))-A_copy,2)
        else:
            Tolerance = input("Enter tolerance to which rank detection should be made: ")
            print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."
            start10_2 = time.clock()
            Reflectors,R,P,computedRankEstimate = TRQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
            end10_2 = time.clock()
            Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])
            # Test deviation from orthogonality
            # Test residual
            print "Computation took ", end10_2-start10_2, " seconds"
            print "Algorithm estimates rank to be - ", computedRankEstimate
            print "Deviation from orthogonality of computed Q - ", la.norm(np.dot(Q[:,:numColumns].T,Q[:,:numColumns])-np.eye(numColumns),2)
            print "Residual - ", la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)
        U2,D2,V2 = la.svd(A_sanity,0)
        for i in range(numColumns-testRank):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        print "Residual of truncated SVD of rank-",testRank," matrix - ", la.norm(A_trunc-A_copy,2)
    else:
        print "You did not specify a valid test."
    
    moreTests = input("Are you done testing? (No - 1, Yes - 0)")
    print "\n\n\n"

In [ ]:
"""
We can also test the 6 rank-detecting algorithms and the numpy SVD side-by-side to compare wallclock time,
  residual of the computed factorization, and detected rank
"""

moreTests = True
while (moreTests):
    
    # Lets create a playground for non-randomized QRCP first
    # Allow them to detect rank, which is important
    # Call the function
    
    numRows = input("Enter number of rows: ")
    numColumns = input("Enter number of columns: ")
    blockSize = input("Enter block size (not relevant for all algorithms): ")
    oversamplingParameter = input("Specify oversampling parameter (not relevant for all algorithms): ")
    # Error check:
    if (blockSize > numColumns):
        print "You cannot enter a blockSize that is greater than the number of columns. Try again"
        continue
    # Error check:
    if (numColumns > numRows):
        print """Sorry. Householder QR does not support matrices that are underdetermined. Good news is I am going to implement
                  the truncated SVD that directly follows from the algorithm: Truncated Randomized Householder QR with column pivoting and no trailing matrix update
                  , so I can update this and give you access to that algorithm in the coming weeks."""
        continue
    A = np.random.rand(numRows, numColumns)
    # I need to change the singular values of A in order to vary the numerical rank
    #   and properly test this method
    U,D,V = la.svd(A,0)
    # D will change, but U and V will not. So we need to save a copy of D
    D_save = D.copy()
    testRankStart = input("Enter the starting rank of the matrix do you want to test with: ")
    # Error check
    if (testRankStart > numColumns):
        print "Requested rank must be less than or equal to numColumns"
        continue
    testRankInterval = input("Enter the interval between ranks that you want to test with: ")
    Tolerance = input("Enter tolerance to which rank detection should be made: ")
    print "Your tolerance is ", Tolerance, ", shown to make sure you know that you specified properly."

    # Create lists to save results in order to create the 3 plots
    rankAxis = []
    qrcpBLAS1_Time = []
    qrcpBLAS1_Rank = []
    qrcpBLAS1_Residual = []
    qrcpBLAS2_Time = []
    qrcpBLAS2_Rank = []
    qrcpBLAS2_Residual = []
    qrcpBLAS3_Time = []
    qrcpBLAS3_Rank = []
    qrcpBLAS3_Residual = []
    ssrqrcp_Time = []
    ssrqrcp_Rank = []
    ssrqrcp_Residual = []
    rsrqrcp_Time = []
    rsrqrcp_Rank = []
    rsrqrcp_Residual = []
    rqrcp_Time = []
    rqrcp_Rank = []
    rqrcp_Residual = []
    trqrcp_Time = []
    trqrcp_Rank = []
    trqrcp_Residual = []
    svd_Time = []
    svd_Rank = []
    svd_Residual = []
    
    while (testRankStart <= numColumns):
        rankAxis.append(testRankStart)
        
        for i in range(testRankStart):
            D[i] = D_save[i]
        for i in range(numColumns-testRankStart):
            D[numColumns-i-1] = 0
        # Re-form A with rank testRank
        tempTrunc1 = np.dot(np.diag(D), V)
        A = np.dot(U, tempTrunc1)
        # Copy A because it is corrupted in function call, yet is needed for residual check 
        A_copy = A.copy()
        A_residual = A.copy()
        print "condition number of matrix A with rank", testRankStart, " is - ", la.cond(A)
        
        # SVD
        startTime = time.clock()
        U2,D2,V2 = la.svd(A,0)
        endTime = time.clock()
        for i in range(numColumns-testRankStart):
            D2[numColumns-i-1] = 0
        tempTrunc2 = np.dot(np.diag(D2), V2)
        A_trunc = np.dot(U2, tempTrunc2)
        svd_Residual.append(la.norm(A_trunc-A,2))
        svd_Rank.append(testRankStart)
        svd_Time.append(endTime-startTime)
        
        # QRCP Blas 1
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS1_version_4(A, Tolerance)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        qrcpBLAS1_Time.append(endTime-startTime)
        qrcpBLAS1_Rank.append(computedRankEstimate)
        qrcpBLAS1_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2)) 
        
        # QRCP Blas 2
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS2_version_4(A, Tolerance)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        qrcpBLAS2_Time.append(endTime-startTime)
        qrcpBLAS2_Rank.append(computedRankEstimate)
        qrcpBLAS2_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2))
        
        # QRCP Blas 3
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = HouseHolderQRCP_BLAS3_version_4(A, blockSize, Tolerance, numColumns)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        qrcpBLAS3_Time.append(endTime-startTime)
        qrcpBLAS3_Rank.append(computedRankEstimate)
        qrcpBLAS3_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2))
        
        # Repeated-sample Randomized QRCP
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = RSRQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        rsrqrcp_Time.append(endTime-startTime)
        rsrqrcp_Rank.append(computedRankEstimate)
        rsrqrcp_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2))
        
        # Randomized QRCP
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = RQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        rqrcp_Time.append(endTime-startTime)
        rqrcp_Rank.append(computedRankEstimate)
        rqrcp_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2))

        # Truncated Randomized QRCP
        A = A_copy.copy()
        startTime = time.clock()
        Reflectors,R,P,computedRankEstimate = TRQRCP_version2(A, blockSize, Tolerance,oversamplingParameter)
        endTime = time.clock()
        Q = convertReflectorsToOrthgonal_version_1(Reflectors[:,:computedRankEstimate])

        trqrcp_Time.append(endTime-startTime)
        trqrcp_Rank.append(computedRankEstimate)
        trqrcp_Residual.append(la.norm(np.dot(Q[:,:computedRankEstimate],np.dot(R[:computedRankEstimate,:],np.eye(numColumns)[:,P].T))-A_copy,2))
        
        testRankStart = testRankStart + testRankInterval

    # Generate plots
    fig1 = ppt.figure(1)
    sub1 = ppt.subplot(111)
    ppt.xlim([rankAxis[0]-10,rankAxis[-1]+10])
    ppt.title('Wall-clock time vs. Matrix rank')
    ppt.xlabel('Matrix rank')
    ppt.ylabel('Wall-clock time (sec)')
    ppt.plot(rankAxis, qrcpBLAS1_Time, 'o', label='qrcpBLAS1')
    ppt.plot(rankAxis, qrcpBLAS2_Time, 'o', label='qrcpBLAS2')
    ppt.plot(rankAxis, qrcpBLAS3_Time, 'o', label='qrcpBLAS3')
    ppt.plot(rankAxis, rsrqrcp_Time, 'o', label='rsrqrcp')
    ppt.plot(rankAxis, rqrcp_Time, 'o', label='rqrcp')
    ppt.plot(rankAxis, trqrcp_Time, 'o', label='trqrcp')
    ppt.plot(rankAxis, svd_Time, 'o', label='svd')
    chartBox = sub1.get_position()
    sub1.set_position([chartBox.x0, chartBox.y0, chartBox.width*0.6, chartBox.height])
    sub1.legend(loc='upper center', bbox_to_anchor=(1.45, 0.8), shadow=True, ncol=1)
    ppt.show()
    
    fig2 = ppt.figure(2)
    sub2 = ppt.subplot(111)
    ppt.xlim([rankAxis[0]-10,rankAxis[-1]+10])
    ppt.title('Rank estimate vs. Matrix rank')
    ppt.xlabel('Matrix rank')
    ppt.ylabel('Rank estimate')
    ppt.plot(rankAxis, qrcpBLAS1_Rank, 'o', label='qrcpBLAS1')
    ppt.plot(rankAxis, qrcpBLAS2_Rank, 'o', label='qrcpBLAS2')
    ppt.plot(rankAxis, qrcpBLAS3_Rank, 'o', label='qrcpBLAS3')
    ppt.plot(rankAxis, rsrqrcp_Rank, 'o', label='rsrqrcp')
    ppt.plot(rankAxis, rqrcp_Rank, 'o', label='rqrcp')
    ppt.plot(rankAxis, trqrcp_Rank, 'o', label='trqrcp')
    ppt.plot(rankAxis, svd_Rank, 'o', label='svd')
    chartBox = sub2.get_position()
    sub2.set_position([chartBox.x0, chartBox.y0, chartBox.width*0.6, chartBox.height])
    sub2.legend(loc='upper center', bbox_to_anchor=(1.45, 0.8), shadow=True, ncol=1)
    ppt.show()
    
    fig3 = ppt.figure(3)
    sub3 = ppt.subplot(111)
    ppt.xlim([rankAxis[0]-10,rankAxis[-1]+10])
    ppt.title('Computed residual vs. Matrix rank')
    ppt.xlabel('Matrix rank')
    ppt.ylabel('Computed residual')
    ppt.plot(rankAxis, qrcpBLAS1_Residual, 'o', label='qrcpBLAS1')
    ppt.plot(rankAxis, qrcpBLAS2_Residual, 'o', label='qrcpBLAS2')
    ppt.plot(rankAxis, qrcpBLAS3_Residual, 'o', label='qrcpBLAS3')
    ppt.plot(rankAxis, rsrqrcp_Residual, 'o', label='rsrqrcp')
    ppt.plot(rankAxis, rqrcp_Residual, 'o', label='rqrcp')
    ppt.plot(rankAxis, trqrcp_Residual, 'o', label='trqrcp')
    ppt.plot(rankAxis, svd_Residual, 'o', label='svd')
    chartBox = sub3.get_position()
    sub3.set_position([chartBox.x0, chartBox.y0, chartBox.width*0.6, chartBox.height])
    sub3.legend(loc='upper center', bbox_to_anchor=(1.45, 0.8), shadow=True, ncol=1)
    ppt.show()
    
    moreTests = input("Are you done testing? (No - 1, Yes - 0)")
    print "\n\n\n"